In [2]:
import os.path

from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import LinearSVC
from sklearn.calibration import CalibratedClassifierCV
from smote_variants import MLPClassifierWrapper

import smote_variants as sv

import pandas as pd
import numpy as np

import imbalanced_databases as imbd
import os, pickle, itertools

In [3]:
# the evaluation procedure uses a directory for caching

cache_path= os.path.join(os.path.expanduser('~'), 'smote_test')

if not os.path.exists(cache_path):
    os.makedirs(cache_path)

In [4]:
# instantiate classifiers
sv_classifiers= [CalibratedClassifierCV(LinearSVC(C=1.0, penalty='l1', loss= 'squared_hinge', dual= False)),
                CalibratedClassifierCV(LinearSVC(C=1.0, penalty='l2', loss= 'hinge', dual= True)),
                CalibratedClassifierCV(LinearSVC(C=1.0, penalty='l2', loss= 'squared_hinge', dual= False)),
                CalibratedClassifierCV(LinearSVC(C=10.0, penalty='l1', loss= 'squared_hinge', dual= False)),
                CalibratedClassifierCV(LinearSVC(C=10.0, penalty='l2', loss= 'hinge', dual= True)),
                CalibratedClassifierCV(LinearSVC(C=10.0, penalty='l2', loss= 'squared_hinge', dual= False))]

mlp_classifiers= []
for x in itertools.product(['relu', 'logistic'], [1.0, 0.5, 0.1]):
    mlp_classifiers.append(MLPClassifierWrapper(activation= x[0], hidden_layer_fraction= x[1]))

nn_classifiers= []
for x in itertools.product([3, 5, 7], ['uniform', 'distance'], [1, 2, 3]):
    nn_classifiers.append(KNeighborsClassifier(n_neighbors= x[0], weights= x[1], p= x[2]))

dt_classifiers= []
for x in itertools.product(['gini', 'entropy'], [None, 3, 5]):
    dt_classifiers.append(DecisionTreeClassifier(criterion= x[0], max_depth= x[1]))

classifiers= []
classifiers.extend(sv_classifiers)
classifiers.extend(mlp_classifiers)
classifiers.extend(nn_classifiers)
classifiers.extend(dt_classifiers)

In [5]:
datas = {}
datas['name'] = 'cleveland-full'
dat = pd.read_csv('cleveland-full.csv')
dat.head()

Age  Sex   Cp  Trestbps   Chol  Fbs  Restecg  Thalach  Exang  Oldpeak  \
0  62.0  1.0  2.0     120.0  281.0  0.0      2.0    103.0    0.0      1.4   
1  60.0  0.0  4.0     150.0  258.0  0.0      2.0    157.0    0.0      2.6   
2  40.0  1.0  4.0     110.0  167.0  0.0      2.0    114.0    1.0      2.0   
3  58.0  1.0  3.0     132.0  224.0  0.0      2.0    173.0    0.0      3.2   
4  54.0  1.0  4.0     110.0  206.0  0.0      2.0    108.0    1.0      0.0   

   Slope   Ca  Thal  output_class  
0    2.0  1.0   7.0             0  
1    2.0  2.0   7.0             0  
2    2.0  0.0   7.0             0  
3    1.0  2.0   7.0             0  
4    2.0  1.0   3.0             0

In [6]:
datas['target'] = dat['output_class'].to_numpy()
dat = dat.drop('output_class', axis=1)
datas['data'] = np.array(dat.values.tolist())

In [7]:
# specifying the classifiers

knn_classifier= KNeighborsClassifier()
dt_classifier= DecisionTreeClassifier()
sv_classifier = CalibratedClassifierCV(LinearSVC())

In [8]:
samplers = [sv.SMOTE, sv.Borderline_SMOTE1, sv.Borderline_SMOTE2, sv.SMOTE_IPF]
results= sv.evaluate_oversamplers(datasets= [datas],
                                    samplers= samplers,
                                    classifiers= classifiers,
                                    cache_path= cache_path,
                                    n_jobs= 10,
                                    max_samp_par_comb=25)

2021-12-07 04:25:42,239:INFO:dataset: cleveland-full, samplings_available: True, evaluations_available: True
2021-12-07 04:25:42,239:INFO:doing the folding
2021-12-07 04:25:42,240:INFO:Folding reading from file folding_cleveland-full.pickle
2021-12-07 04:25:42,242:INFO:do the samplings
2021-12-07 04:25:42,243:INFO:create sampling objects, random_state: 
2021-12-07 04:25:42,243:INFO:samplers: [<class 'smote_variants._smote_variants.SMOTE'>, <class 'smote_variants._smote_variants.Borderline_SMOTE1'>, <class 'smote_variants._smote_variants.Borderline_SMOTE2'>, <class 'smote_variants._smote_variants.SMOTE_IPF'>]
2021-12-07 04:25:42,244:INFO:[{'n_neighbors': 3, 'proportion': 0.1}, {'n_neighbors': 3, 'proportion': 0.25}, {'n_neighbors': 3, 'proportion': 0.5}, {'n_neighbors': 3, 'proportion': 0.75}, {'n_neighbors': 3, 'proportion': 1.0}, {'n_neighbors': 3, 'proportion': 1.5}, {'n_neighbors': 3, 'proportion': 2.0}, {'n_neighbors': 5, 'proportion': 0.1}, {'n_neighbors': 5, 'proportion': 0.25}, 

["('cleveland-full', OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 7), ('p', 0.01), ('proportion', 2.0), ('random_state', None), ('voting', 'consensus')]), 'CalibratedClassifierCV', OrderedDict([('base_estimator', LinearSVC(dual=False, penalty='l1')), ('base_estimator__C', 1.0), ('base_estimator__class_weight', None), ('base_estimator__dual', False), ('base_estimator__fit_intercept', True), ('base_estimator__intercept_scaling', 1), ('base_estimator__loss', 'squared_hinge'), ('base_estimator__max_iter', 1000), ('base_estimator__multi_class', 'ovr'), ('base_estimator__penalty', 'l1'), ('base_estimator__random_state', None), ('base_estimator__tol', 0.0001), ('base_estimator__verbose', 0), ('cv', None), ('ensemble', True), ('method', 'sigmoid'), ('n_jobs', None)]))", "('cleveland-full', OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 7), ('p', 0.01), ('proportion'

2021-12-07 04:25:44,406:INFO:Sampling sampler parameter string OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 3), ('p', 0.01), ('proportion', 1.5), ('random_state', None), ('voting', 'majority')])
2021-12-07 04:25:44,418:INFO:{'classifier': DecisionTreeClassifier(random_state=2), 'k': 3, 'n_folds': 9, 'n_neighbors': 3, 'p': 0.01, 'proportion': 1.5, 'voting': 'consensus', 'random_state': None}
2021-12-07 04:25:44,419:INFO:Sampling sampler parameter string OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 3), ('p', 0.01), ('proportion', 1.5), ('random_state', None), ('voting', 'consensus')])
2021-12-07 04:25:44,433:INFO:{'classifier': DecisionTreeClassifier(random_state=2), 'k': 3, 'n_folds': 9, 'n_neighbors': 5, 'p': 0.01, 'proportion': 1.5, 'voting': 'majority', 'random_state': None}
2021-12-07 04:25:44,435:INFO:Sampling sampler parameter string OrderedDict([('cl

["('cleveland-full', OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 3), ('p', 0.01), ('proportion', 1.5), ('random_state', None), ('voting', 'majority')]), 'CalibratedClassifierCV', OrderedDict([('base_estimator', LinearSVC(dual=False, penalty='l1')), ('base_estimator__C', 1.0), ('base_estimator__class_weight', None), ('base_estimator__dual', False), ('base_estimator__fit_intercept', True), ('base_estimator__intercept_scaling', 1), ('base_estimator__loss', 'squared_hinge'), ('base_estimator__max_iter', 1000), ('base_estimator__multi_class', 'ovr'), ('base_estimator__penalty', 'l1'), ('base_estimator__random_state', None), ('base_estimator__tol', 0.0001), ('base_estimator__verbose', 0), ('cv', None), ('ensemble', True), ('method', 'sigmoid'), ('n_jobs', None)]))", "('cleveland-full', OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 3), ('p', 0.01), ('proportion',

2021-12-07 04:25:44,625:INFO:Sampling sampler parameter string OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 3), ('p', 0.01), ('proportion', 0.75), ('random_state', None), ('voting', 'consensus')])
2021-12-07 04:25:44,637:INFO:{'classifier': DecisionTreeClassifier(random_state=2), 'k': 3, 'n_folds': 9, 'n_neighbors': 7, 'p': 0.01, 'proportion': 0.75, 'voting': 'majority', 'random_state': None}
2021-12-07 04:25:44,638:INFO:Sampling sampler parameter string OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 7), ('p', 0.01), ('proportion', 0.75), ('random_state', None), ('voting', 'majority')])
2021-12-07 04:25:44,651:INFO:{'k_neighbors': 5, 'n_neighbors': 3, 'proportion': 0.75, 'random_state': None}
2021-12-07 04:25:44,651:INFO:Sampling sampler parameter string OrderedDict([('k_neighbors', 5), ('n_neighbors', 3), ('proportion', 0.75), ('random_state', None)])
2021-

...

2021-12-07 04:25:44,837:INFO:{'k_neighbors': 5, 'n_neighbors': 3, 'proportion': 0.5, 'random_state': None}
2021-12-07 04:25:44,841:INFO:Sampling sampler parameter string OrderedDict([('k_neighbors', 5), ('n_neighbors', 3), ('proportion', 0.5), ('random_state', None)])
2021-12-07 04:25:44,848:INFO:{'k_neighbors': 3, 'n_neighbors': 7, 'proportion': 0.5, 'random_state': None}
2021-12-07 04:25:44,848:INFO:Sampling sampler parameter string OrderedDict([('k_neighbors', 3), ('n_neighbors', 7), ('proportion', 0.5), ('random_state', None)])
2021-12-07 04:25:44,855:INFO:{'k_neighbors': 7, 'n_neighbors': 7, 'proportion': 0.5, 'random_state': None}
2021-12-07 04:25:44,856:INFO:Sampling sampler parameter string OrderedDict([('k_neighbors', 7), ('n_neighbors', 7), ('proportion', 0.5), ('random_state', None)])
2021-12-07 04:25:44,864:INFO:{'k_neighbors': 7, 'n_neighbors': 3, 'proportion': 0.5, 'random_state': None}
2021-12-07 04:25:44,865:INFO:Sampling sampler parameter string OrderedDict([('k_neighb

["('cleveland-full', OrderedDict([('k_neighbors', 5), ('n_neighbors', 3), ('proportion', 0.5), ('random_state', None)]), 'CalibratedClassifierCV', OrderedDict([('base_estimator', LinearSVC(dual=False, penalty='l1')), ('base_estimator__C', 1.0), ('base_estimator__class_weight', None), ('base_estimator__dual', False), ('base_estimator__fit_intercept', True), ('base_estimator__intercept_scaling', 1), ('base_estimator__loss', 'squared_hinge'), ('base_estimator__max_iter', 1000), ('base_estimator__multi_class', 'ovr'), ('base_estimator__penalty', 'l1'), ('base_estimator__random_state', None), ('base_estimator__tol', 0.0001), ('base_estimator__verbose', 0), ('cv', None), ('ensemble', True), ('method', 'sigmoid'), ('n_jobs', None)]))", "('cleveland-full', OrderedDict([('k_neighbors', 5), ('n_neighbors', 3), ('proportion', 0.5), ('random_state', None)]), 'CalibratedClassifierCV', OrderedDict([('base_estimator', LinearSVC(loss='hinge')), ('base_estimator__C', 1.0), ('base_estimator__class_weigh

2021-12-07 04:25:45,062:INFO:{'classifier': DecisionTreeClassifier(random_state=2), 'k': 3, 'n_folds': 9, 'n_neighbors': 5, 'p': 0.01, 'proportion': 0.1, 'voting': 'majority', 'random_state': None}
2021-12-07 04:25:45,063:INFO:Sampling sampler parameter string OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 5), ('p', 0.01), ('proportion', 0.1), ('random_state', None), ('voting', 'majority')])
2021-12-07 04:25:45,074:INFO:{'classifier': DecisionTreeClassifier(random_state=2), 'k': 3, 'n_folds': 9, 'n_neighbors': 3, 'p': 0.01, 'proportion': 0.1, 'voting': 'majority', 'random_state': None}
2021-12-07 04:25:45,076:INFO:Sampling sampler parameter string OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 3), ('p', 0.01), ('proportion', 0.1), ('random_state', None), ('voting', 'majority')])
2021-12-07 04:25:45,088:INFO:{'k_neighbors': 5, 'n_neighbors': 3, 'proportion': 0.


["('cleveland-full', OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 5), ('p', 0.01), ('proportion', 0.1), ('random_state', None), ('voting', 'majority')]), 'CalibratedClassifierCV', OrderedDict([('base_estimator', LinearSVC(dual=False, penalty='l1')), ('base_estimator__C', 1.0), ('base_estimator__class_weight', None), ('base_estimator__dual', False), ('base_estimator__fit_intercept', True), ('base_estimator__intercept_scaling', 1), ('base_estimator__loss', 'squared_hinge'), ('base_estimator__max_iter', 1000), ('base_estimator__multi_class', 'ovr'), ('base_estimator__penalty', 'l1'), ('base_estimator__random_state', None), ('base_estimator__tol', 0.0001), ('base_estimator__verbose', 0), ('cv', None), ('ensemble', True), ('method', 'sigmoid'), ('n_jobs', None)]))", "('cleveland-full', OrderedDict([('classifier', DecisionTreeClassifier(random_state=2)), ('k', 3), ('n_folds', 9), ('n_neighbors', 5), ('p', 0.01), ('proportion'

2021-12-07 04:25:45,569:INFO:Evaluation do the evaluation cleveland-full Borderline_SMOTE2 CalibratedClassifierCV
2021-12-07 04:25:45,574:INFO:Evaluation do the evaluation cleveland-full Borderline_SMOTE2 CalibratedClassifierCV
/home/nmc/anaconda3/envs/deeplearning/lib/python3.9/site-packages/sklearn/svm/_base.py:1199: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/home/nmc/anaconda3/envs/deeplearning/lib/python3.9/site-packages/sklearn/svm/_base.py:1199: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/home/nmc/anaconda3/envs/deeplearning/lib/python3.9/site-packages/sklearn/svm/_base.py:1199: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/home/nmc/anaconda3/envs/deeplearning/lib/python3.9/site-packages/sklearn/svm/_base.py:1199: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warning

In [9]:
highest_auc_score= results['auc'].idxmax()
print(highest_auc_score)

15


In [10]:
print(results.columns)
print("------------------------")
print(results)

Index(['db_name', 'classifier', 'sampler', 'auc', 'auc_mean', 'auc_std',
       'brier', 'acc', 'f1', 'p_top20', 'gacc', 'runtime', 'db_size',
       'db_n_attr', 'imbalanced_ratio', 'sampler_categories',
       'classifier_parameters_auc', 'classifier_parameters_acc',
       'classifier_parameters_gacc', 'classifier_parameters_f1',
       'classifier_parameters_p_top20', 'classifier_parameters_brier',
       'sampler_parameters_auc', 'sampler_parameters_acc',
       'sampler_parameters_gacc', 'sampler_parameters_f1',
       'sampler_parameters_p_top20', 'sampler_parameters_brier'],
      dtype='object')
------------------------
           db_name              classifier            sampler       auc  \
0   cleveland-full  CalibratedClassifierCV  Borderline_SMOTE1  0.808627   
1   cleveland-full  CalibratedClassifierCV  Borderline_SMOTE2  0.804726   
2   cleveland-full  CalibratedClassifierCV              SMOTE  0.823725   
3   cleveland-full  CalibratedClassifierCV          SMOTE_IPF  

In [11]:
print(results[['db_name', 'classifier', 'sampler', 'auc']].to_html('cleveland-full.html'))

None
